In [1]:
# Extraindo um frame de um vídeo

import cv2

video_path = "D:/Faculdade/TCC/VideosGestos/abacaxi/SignBank_ABACAXI.mp4"

cap = cv2.VideoCapture(video_path)

# Indica que devera ser capturado o frame de número 51 do video
cap.set(cv2.CAP_PROP_POS_FRAMES, 50)

# Verifica se o vídeo foi aberto corretamente
if not cap.isOpened():
    print("Erro ao abrir o vídeo.")

# Lê o frame
ret, frame = cap.read()

# Verifica se o frame foi lido corretamente
if not ret:
    print(f"Erro ao ler o frame.")

# Exibe o frame
cv2.imshow('Frame', frame)
cv2.waitKey(0)
cap.release()
cv2.destroyAllWindows()

In [9]:
import mediapipe as mp
import numpy as np
import cv2

video_path = "D:/Faculdade/TCC/VideosGestos/abacaxi/SignBank_ABACAXI.mp4"

# Variavel para auxiliar na exibição dos landmarks
mp_drawing = mp.solutions.drawing_utils
# Variavel para auxiliar na extração dos landmarks das mãos, rosto e corpo
mp_holistic = mp.solutions.holistic
# Abre o vídeo
cap = cv2.VideoCapture(video_path)

# Como o with funciona: Ele chama o método __enter__ da classe, executa o bloco de código e chama o método __exit__ da classe -> ideal para usar recursos que precisam ser inicializados e finalizados
# min_detection_confidence: confiança mínima para que um landmark seja considerado detectado
# detection: Processo de identificar a presença e localização de um landmark 
# min_tracking_confidence: confiança mínima para que um landmark seja considerado rastreado
# tracking: Processo de seguir o landmark ao longo do tempo em diferentes quadros de um vídeo.
with mp_holistic.Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5) as holistic:
    # Enquanto o vídeo estiver aberto
    while cap.isOpened():
        # Lê o proximo frame do vídeo
        ret, frame = cap.read()
        # Se não houver mais frames, sai do loop
        if not ret:
            break
        
        # Cria uma imagem com as mesmas dimensões do frame
        img = np.zeros((frame.shape[0], frame.shape[1], frame.shape[2]))
        # Converte o frame de BGR (formato padrão do  do OpenCV) para RGB (formato padrão do Mediapipe)
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        # Define a flag do frame como não gravável para garantir a segurança ao passar o frame para a Mediapipe
        frame.flags.writeable = False

        # Processa o frame
        results = holistic.process(frame)

        # Desenha os landmarks do rosto, mãos e corpo no frame img
        mp_drawing.draw_landmarks(img, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS,
                                    mp_drawing.DrawingSpec(color=(255, 255, 0), thickness=2, circle_radius=1),
                                    mp_drawing.DrawingSpec(color=(255, 0, 0), thickness=2))
        mp_drawing.draw_landmarks(img, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS,
                                    mp_drawing.DrawingSpec(color=(0, 255, 0), thickness=2, circle_radius=1),
                                    mp_drawing.DrawingSpec(color=(57, 143, 0), thickness=2))
        mp_drawing.draw_landmarks(img, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS,
                                    mp_drawing.DrawingSpec(color=(128, 0, 255), thickness=2, circle_radius=1),
                                    mp_drawing.DrawingSpec(color=(255, 255, 255), thickness=2))

        # Converte a imagem de RGB para BGR
        frame = cv2.cvtColor(frame, cv2.COLOR_RGB2BGR)
        # Exibe o frame com os landmarks
        cv2.imshow("Landmarks", img)

        # Se a tecla 'q' for pressionada, sai do loop
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

# Libera o vídeo e fecha todas as janelas
cap.release()
cv2.destroyAllWindows()

In [1]:
import mediapipe as mp
import cv2
import numpy as np

video_path = "D:/Faculdade/TCC/VideosGestos/abacaxi/SignBank_ABACAXI.mp4"

mp_holistic = mp.solutions.holistic

cap = cv2.VideoCapture(video_path)

with mp_holistic.Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5) as holistic:
    frame_id = 0
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = cap.get(cv2.CAP_PROP_FPS)
    duration = frame_count / fps

    #print(f"Duration: {duration} seconds")
    #print(f"FPS: {fps}")
    
    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        img = np.zeros((frame.shape[0], frame.shape[1], frame.shape[2]))
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        frame.flags.writeable = False

        results = holistic.process(frame)

        if results.pose_landmarks:
            for landmark_id, landmark in enumerate(results.pose_landmarks.landmark):
                landmark_info = f"frame: {frame_id}, row_id: {frame_id}-pose-{landmark_id}, type: pose, landmark_index: {landmark_id}, X: {landmark.x}, Y: {landmark.y}, Z: {landmark.z}"
                print(landmark_info)

        if results.left_hand_landmarks:
            for landmark_id, landmark in enumerate(results.left_hand_landmarks.landmark):
                landmark_info = f"frame: {frame_id}, row_id: {frame_id}-left_hand-{landmark_id}, type: left_hand, landmark_index: {landmark_id}, X: {landmark.x}, Y: {landmark.y}, Z: {landmark.z}"
                print(landmark_info)

        if results.right_hand_landmarks:
            for landmark_id, landmark in enumerate(results.right_hand_landmarks.landmark):
                landmark_info = f"frame: {frame_id}, row_id: {frame_id}-right_hand-{landmark_id}, type: right_hand, landmark_index: {landmark_id}, X: {landmark.x}, Y: {landmark.y}, Z: {landmark.z}"
                print(landmark_info)

        if results.face_landmarks:
            for landmark_id, landmark in enumerate(results.face_landmarks.landmark):
                landmark_info = f"frame: {frame_id}, row_id: {frame_id}-face-{landmark_id}, type: face, landmark_index: {landmark_id}, X: {landmark.x}, Y: {landmark.y}, Z: {landmark.z}"
                print(landmark_info)

        frame_id += 1

cap.release()
cv2.destroyAllWindows()


frame: 0, row_id: 0-pose-0, type: pose, landmark_index: 0, X: 0.5038180351257324, Y: 0.3241357207298279, Z: -0.6993166208267212
frame: 0, row_id: 0-pose-1, type: pose, landmark_index: 1, X: 0.517261266708374, Y: 0.28985708951950073, Z: -0.6672766804695129
frame: 0, row_id: 0-pose-2, type: pose, landmark_index: 2, X: 0.523840606212616, Y: 0.2904268503189087, Z: -0.6673192381858826
frame: 0, row_id: 0-pose-3, type: pose, landmark_index: 3, X: 0.5312754511833191, Y: 0.2906222939491272, Z: -0.6672813892364502
frame: 0, row_id: 0-pose-4, type: pose, landmark_index: 4, X: 0.490406334400177, Y: 0.2925795912742615, Z: -0.6665053963661194
frame: 0, row_id: 0-pose-5, type: pose, landmark_index: 5, X: 0.4815467894077301, Y: 0.294966459274292, Z: -0.6666358113288879
frame: 0, row_id: 0-pose-6, type: pose, landmark_index: 6, X: 0.4745333790779114, Y: 0.29822319746017456, Z: -0.6669026017189026
frame: 0, row_id: 0-pose-7, type: pose, landmark_index: 7, X: 0.5423992872238159, Y: 0.3084011673927307, Z

In [5]:
# Processa os landmarks no formato da competicao (1 linha por landmark)

import os
import mediapipe as mp
import cv2
import numpy as np
import csv

mp_holistic = mp.solutions.holistic.Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5)

# Função para percorrer recursivamente os arquivos de uma pasta
def get_videos(folder):
    videos = []
    for root, dirs, files in os.walk(folder):
        for file in files:
            if file.endswith(".mp4"):
                videos.append(os.path.join(root, file))
    return videos

video_folder = "D:/Faculdade/TCC/VideosGestos"
videos = get_videos(video_folder)
video_id = 0

def process_landmarks(results, frame_id, frame_type, video_folder, video_name):
    if results:
        with open('landmarks.csv', mode='a', newline='') as file:
            writer = csv.writer(file)
            for landmark_id, landmark in enumerate(results.landmark):
                row_id = f"{video_id}-{video_folder}-{frame_id}-{frame_type}-{landmark_id}"
                row = [row_id, video_name, video_id, video_folder, frame_id, frame_type, landmark_id, landmark.x, landmark.y, landmark.z]
                writer.writerow(row)

for video_path in videos:
    video_name = os.path.basename(video_path)
    video_folder = os.path.basename(os.path.dirname(video_path))

    print(f"Processando o vídeo: {video_name} na pasta: {video_folder}")

    cap = cv2.VideoCapture(video_path)

    frame_id = 0  # Contador para o número do frame

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        img = np.zeros((frame.shape[0], frame.shape[1], frame.shape[2]))
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        frame.flags.writeable = False

        results = mp_holistic.process(frame)

        process_landmarks(results.pose_landmarks, frame_id, 'pose', video_folder, video_name)
        process_landmarks(results.left_hand_landmarks, frame_id, 'left_hand', video_folder, video_name)
        process_landmarks(results.right_hand_landmarks, frame_id, 'right_hand', video_folder, video_name)
        process_landmarks(results.face_landmarks, frame_id, 'face', video_folder, video_name)

        frame_id += 1

    cap.release()
    video_id += 1

cv2.destroyAllWindows()


Processando o vídeo: INES_abacaxi.mp4 na pasta: abacaxi
Processando o vídeo: SignBank_ABACAXI.mp4 na pasta: abacaxi
Processando o vídeo: UFPE_20210127091036_6011583c87073.mp4 na pasta: abacaxi
Processando o vídeo: UFPE_20210128115432_601378e8d032d.mp4 na pasta: abacaxi
Processando o vídeo: UFPE_20210929043133_6154bf1508f4a.mp4 na pasta: abacaxi
Processando o vídeo: UFV_abacaxi.mp4 na pasta: abacaxi
Processando o vídeo: INES_acompanhar1.mp4 na pasta: acompanhar
Processando o vídeo: INES_acompanhar2.mp4 na pasta: acompanhar
Processando o vídeo: SignBank_ACOMPANHAR.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_20201221020919_5fe0d6bfd692f.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_20201221020919_5fe0d6bfe16a7.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_20210331111458_606483e2cc0bc.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_ligia-25-Acompanhar.mp4 na pasta: acompanhar
Processando o vídeo: UFV_01558-Acompanhar.mp4 na pasta: acompanhar
Processando o vídeo: INES_ac

In [5]:
# Processa os landmarks no formato de um frame por linha

import os
import mediapipe as mp
import cv2
import numpy as np
import csv
import math

mp_holistic = mp.solutions.holistic.Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5)

# Função para percorrer recursivamente os arquivos de uma pasta
def get_videos(folder):
    videos = []
    for root, dirs, files in os.walk(folder):
        for file in files:
            if file.endswith(".mp4"):
                videos.append(os.path.join(root, file))
    return videos

video_folder = "D:/Faculdade/TCC/VideosGestos"
videos = get_videos(video_folder)
video_id = 0

def process_landmarks(results, frame_id, frame_type, video_folder, video_name):
    if results:
        with open('landmarks.csv', mode='a', newline='') as file:
            writer = csv.writer(file)
            row_id = f"{video_id}-{video_folder}-{frame_id}-{frame_type}"
            row = [row_id, video_name, video_id, video_folder, frame_id, frame_type]
            for landmark_id, landmark in enumerate(results.landmark):
                row.extend([landmark.x, landmark.y, landmark.z])

            writer.writerow(row)

for video_path in videos:
    """
    if video_id > 10:
        break
    """

    video_name = os.path.basename(video_path)
    video_folder = os.path.basename(os.path.dirname(video_path))

    print(f"Processando o vídeo: {video_name} na pasta: {video_folder}")

    cap = cv2.VideoCapture(video_path)

    frame_id = 0  # Contador para o número do frame

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        img = np.zeros((frame.shape[0], frame.shape[1], frame.shape[2]))
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        frame.flags.writeable = False

        results = mp_holistic.process(frame)

        if results:
            with open('landmarks.csv', mode='a', newline='') as file:
                writer = csv.writer(file)
                row_id = f"{video_id}-{video_folder}-{frame_id}"
                row = [row_id, video_name, video_id, video_folder, frame_id]

                if results.pose_landmarks:
                    for landmark_id, landmark in enumerate(results.pose_landmarks.landmark):
                        row.extend([landmark.x, landmark.y, landmark.z])
                else:
                    row.extend([math.nan] * 33 * 3)
                    
                if results.left_hand_landmarks:
                    for landmark_id, landmark in enumerate(results.left_hand_landmarks.landmark):
                        row.extend([landmark.x, landmark.y, landmark.z])
                else:
                    row.extend([math.nan] * 21 * 3) 

                if results.right_hand_landmarks:
                    for landmark_id, landmark in enumerate(results.right_hand_landmarks.landmark):
                        row.extend([landmark.x, landmark.y, landmark.z])
                else:
                    row.extend([math.nan] * 21 * 3) 
                    
                # Não irei processar os landmarks do rosto
                writer.writerow(row)

        frame_id += 1

    cap.release()
    video_id += 1

cv2.destroyAllWindows()


Processando o vídeo: INES_abacaxi.mp4 na pasta: abacaxi
Processando o vídeo: SignBank_ABACAXI.mp4 na pasta: abacaxi
Processando o vídeo: UFPE_20210127091036_6011583c87073.mp4 na pasta: abacaxi
Processando o vídeo: UFPE_20210128115432_601378e8d032d.mp4 na pasta: abacaxi
Processando o vídeo: UFPE_20210929043133_6154bf1508f4a.mp4 na pasta: abacaxi
Processando o vídeo: UFV_abacaxi.mp4 na pasta: abacaxi
Processando o vídeo: INES_acompanhar1.mp4 na pasta: acompanhar
Processando o vídeo: INES_acompanhar2.mp4 na pasta: acompanhar
Processando o vídeo: SignBank_ACOMPANHAR.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_20201221020919_5fe0d6bfd692f.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_20201221020919_5fe0d6bfe16a7.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_20210331111458_606483e2cc0bc.mp4 na pasta: acompanhar
Processando o vídeo: UFPE_ligia-25-Acompanhar.mp4 na pasta: acompanhar
Processando o vídeo: UFV_01558-Acompanhar.mp4 na pasta: acompanhar
Processando o vídeo: INES_ac

In [4]:
import pandas as pd
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

landmarks = pd.read_csv('landmarks.csv', header=None, sep=',')
landmarks.head(10)

0                 1    2        3    4         5         6    \
0  0-abacaxi-0  INES_abacaxi.mp4    0  abacaxi    0  0.495696  0.251119   
1  0-abacaxi-1  INES_abacaxi.mp4    0  abacaxi    1  0.495288  0.252841   
2  0-abacaxi-2  INES_abacaxi.mp4    0  abacaxi    2  0.495044  0.253372   
3  0-abacaxi-3  INES_abacaxi.mp4    0  abacaxi    3  0.495121  0.253392   
4  0-abacaxi-4  INES_abacaxi.mp4    0  abacaxi    4  0.495188  0.252976   
5  0-abacaxi-5  INES_abacaxi.mp4    0  abacaxi    5  0.495208  0.251434   
6  0-abacaxi-6  INES_abacaxi.mp4    0  abacaxi    6  0.495229  0.250174   
7  0-abacaxi-7  INES_abacaxi.mp4    0  abacaxi    7  0.495766  0.248833   
8  0-abacaxi-8  INES_abacaxi.mp4    0  abacaxi    8  0.497829  0.248504   
9  0-abacaxi-9  INES_abacaxi.mp4    0  abacaxi    9  0.503484  0.245884   

        7         8         9         10        11        12        13   \
0 -1.002079  0.521189  0.209761 -0.950463  0.533843  0.210290 -0.950714   
1 -1.023815  0.520663  0.213098 -0.972513  0.533857  0.213758 -0.972775   
2 -1.046565  0.520381  0.214643 -0.995046  0.533899  0.215396 -0.995281   
3 -1.043955  0.520395  0.214777 -0.992153  0.534221  0.215514 -0.992404   
4 -1.012853  0.520400  0.214682 -0.960610  0.534458  0.215453 -0.960871   
5 -1.012929  0.520392  0.213540 -0.959802  0.534535  0.214476 -0.960124   
6 -1.022770  0.520350  0.212143 -0.967764  0.534544  0.213149 -0.968192   
7 -0.914387  0.520518  0.209700 -0.857555  0.534744  0.210621 -0.858042   
8 -0.857688  0.521871  0.207812 -0.804868  0.535753  0.208698 -0.805205   
9 -0.639969  0.526488  0.204478 -0.583603  0.538848  0.205509 -0.583859   

        14        15        16        17        18        19        20   \
0  0.545261  0.212878 -0.950727  0.475877  0.212704 -0.947200  0.463136   
1  0.545182  0.215439 -0.972803  0.475431  0.215584 -0.967649  0.462078   
2  0.545160  0.216666 -0.995289  0.475202  0.216619 -0.990622  0.461485   
3  0.545196  0.216702 -0.992438  0.475215  0.216841 -0.988482  0.461473   
4  0.545223  0.216593 -0.960911  0.475224  0.216627 -0.957046  0.461457   
5  0.545222  0.215676 -0.960155  0.475229  0.214756 -0.956536  0.461449   
6  0.545190  0.214456 -0.968223  0.475251  0.213248 -0.966737  0.461452   
7  0.545252  0.211909 -0.857981  0.475613  0.211847 -0.858578  0.461809   
8  0.545834  0.209971 -0.804946  0.477233  0.210758 -0.802870  0.463545   
9  0.548631  0.206759 -0.583428  0.480835  0.207990 -0.578459  0.466475   

        21        22        23        24        25        26        27   \
0  0.214114 -0.947133  0.449410  0.217801 -0.947687  0.568593  0.239211   
1  0.217285 -0.967517  0.449261  0.219710 -0.968047  0.568426  0.241346   
2  0.218336 -0.990460  0.449155  0.220254 -0.990963  0.568391  0.242590   
3  0.218645 -0.988361  0.449155  0.220443 -0.988881  0.568374  0.242763   
4  0.218357 -0.956863  0.449151  0.220112 -0.957363  0.568372  0.242768   
5  0.216080 -0.956425  0.449149  0.218082 -0.956960  0.568355  0.242383   
6  0.214525 -0.966820  0.449149  0.216777 -0.967454  0.568301  0.241919   
7  0.213493 -0.858780  0.449294  0.216081 -0.859550  0.568346  0.240592   
8  0.212677 -0.802922  0.450187  0.215469 -0.803510  0.568626  0.239379   
9  0.209937 -0.578449  0.451855  0.212830 -0.579015  0.570402  0.236727   

        28        29        30        31        32        33        34   \
0 -0.606676  0.438194  0.247255 -0.582871  0.526797  0.307200 -0.875365   
1 -0.622200  0.438184  0.247786 -0.589336  0.526384  0.308975 -0.894940   
2 -0.642147  0.438184  0.247866 -0.609594  0.526088  0.309600 -0.917403   
3 -0.640178  0.438197  0.247868 -0.611365  0.526090  0.309667 -0.914945   
4 -0.613345  0.438202  0.247498 -0.584008  0.526091  0.309416 -0.886539   
5 -0.609033  0.438217  0.246393 -0.583084  0.526076  0.308196 -0.885840   
6 -0.614730  0.438295  0.245701 -0.600410  0.526040  0.307131 -0.893500   
7 -0.506739  0.438686  0.245333 -0.499276  0.526333  0.305874 -0.785139   
8 -0.450991  0.439418  0.244831 

In [5]:
import pandas as pd

df_landmarks = pd.read_csv('landmarks.csv', header=None, sep=',')

# Criando os nomes das colunas
colunas = ['row_id', 'video_name', 'video_id', 'class', 'frame_id']
for i in range(33):
    colunas.extend([f'pose_x_{i}', f'pose_y_{i}', f'pose_z_{i}'])
for i in range(21):
    colunas.extend([f'left_hand_x_{i}', f'left_hand_y_{i}', f'left_hand_z_{i}'])
for i in range(21):
    colunas.extend([f'right_hand_x_{i}', f'right_hand_y_{i}', f'right_hand_z_{i}'])


print(df_landmarks.shape)
print(len(colunas))

(46894, 230)
230


In [8]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

df_landmarks.columns = colunas
df_landmarks.head(5)

row_id        video_name  video_id    class  frame_id  pose_x_0  \
0  0-abacaxi-0  INES_abacaxi.mp4         0  abacaxi         0  0.495696   
1  0-abacaxi-1  INES_abacaxi.mp4         0  abacaxi         1  0.495288   
2  0-abacaxi-2  INES_abacaxi.mp4         0  abacaxi         2  0.495044   
3  0-abacaxi-3  INES_abacaxi.mp4         0  abacaxi         3  0.495121   
4  0-abacaxi-4  INES_abacaxi.mp4         0  abacaxi         4  0.495188   

   pose_y_0  pose_z_0  pose_x_1  pose_y_1  pose_z_1  pose_x_2  pose_y_2  \
0  0.251119 -1.002079  0.521189  0.209761 -0.950463  0.533843  0.210290   
1  0.252841 -1.023815  0.520663  0.213098 -0.972513  0.533857  0.213758   
2  0.253372 -1.046565  0.520381  0.214643 -0.995046  0.533899  0.215396   
3  0.253392 -1.043955  0.520395  0.214777 -0.992153  0.534221  0.215514   
4  0.252976 -1.012853  0.520400  0.214682 -0.960610  0.534458  0.215453   

   pose_z_2  pose_x_3  pose_y_3  pose_z_3  pose_x_4  pose_y_4  pose_z_4  \
0 -0.950714  0.545261  0.212878 -0.950727  0.475877  0.212704 -0.947200   
1 -0.972775  0.545182  0.215439 -0.972803  0.475431  0.215584 -0.967649   
2 -0.995281  0.545160  0.216666 -0.995289  0.475202  0.216619 -0.990622   
3 -0.992404  0.545196  0.216702 -0.992438  0.475215  0.216841 -0.988482   
4 -0.960871  0.545223  0.216593 -0.960911  0.475224  0.216627 -0.957046   

   pose_x_5  pose_y_5  pose_z_5  pose_x_6  pose_y_6  pose_z_6  pose_x_7  \
0  0.463136  0.214114 -0.947133  0.449410  0.217801 -0.947687  0.568593   
1  0.462078  0.217285 -0.967517  0.449261  0.219710 -0.968047  0.568426   
2  0.461485  0.218336 -0.990460  0.449155  0.220254 -0.990963  0.568391   
3  0.461473  0.218645 -0.988361  0.449155  0.220443 -0.988881  0.568374   
4  0.461457  0.218357 -0.956863  0.449151  0.220112 -0.957363  0.568372   

   pose_y_7  pose_z_7  pose_x_8  pose_y_8  pose_z_8  pose_x_9  pose_y_9  \
0  0.239211 -0.606676  0.438194  0.247255 -0.582871  0.526797  0.307200   
1  0.241346 -0.622200  0.438184  0.247786 -0.589336  0.526384  0.308975   
2  0.242590 -0.642147  0.438184  0.247866 -0.609594  0.526088  0.309600   
3  0.242763 -0.640178  0.438197  0.247868 -0.611365  0.526090  0.309667   
4  0.242768 -0.613345  0.438202  0.247498 -0.584008  0.526091  0.309416   

   pose_z_9  pose_x_10  pose_y_10  pose_z_10  pose_x_11  pose_y_11  pose_z_11  \
0 -0.875365   0.471233   0.309380  -0.868394   0.678584   0.549230  -0.385215   
1 -0.894940   0.469505   0.311069  -0.885050   0.678677   0.549743  -0.396438   
2 -0.917403   0.468491   0.311584  -0.907750   0.678793   0.550119  -0.412349   
3 -0.914945   0.468413   0.311771  -0.906412   0.678798   0.550017  -0.412191   
4 -0.886539   0.468346   0.311608  -0.877740   0.678863   0.549439  -0.396280   

   pose_x_12  pose_y_12  pose_z_12  pose_x_13  pose_y_13  pose_z_13  \
0   0.340820   0.535919  -0.348497   0.732885   0.914818  -0.342786   
1   0.340721   0.535921  -0.355200   0.732540   0.917953  -0.342048   
2   0.340644   0.535930  -0.383089   0.732493   0.920810  -0.345079   
3   0.340651   0.536010  -0.384030   0.732280   0.921365  -0.346550   
4   0.340753   0.536106  -0.374324   0.731608   0.921345  -0.327906   

   pose_x_14  pose_y_14  pose_z_14  pose_x_15  pose_y_15  pose_z_15  \
0   0.284963   0.897970  -0.278457   0.760130   1.175227  -0.769186   
1   0.284964   0.898140  -0.278857   0.760292   1.188829  -0.748641   
2   0.284964   0.898274  -0.300990   0.761115   1.196293  -0.747695   
3   0.285392   0.898343  -0.304133   0.758980   1.195107  -0.749362   
4   0.285404   0.900387  -0.296143   0.756870   1.194275  -0.724050   

   pose_x_16  pose_y_16  pose_z_16  pose_x_17  pose_y_17  pose_z_17  \
0   0.243029   1.153512  -0.695576   0.773915   1.271270  -0.890982   
1   0.243005   1.153649  -0.696378   0.774294   1.286058  -0.869075   
2   0.242966   1.158451  -0.713334   0.775510   1.294023  -0.867836   
3   0.244254   1.159555  -0.715063   0.773296   1.293015  -0.869765   
4   0.246114   1.159675  -0.703363   0.768647   1.291963 

In [10]:
# Descritivo dos dados apenas min e max
df_landmarks.describe().loc[['min', 'max']]

video_id  frame_id  pose_x_0  pose_y_0  pose_z_0  pose_x_1  pose_y_1  \
min       0.0       0.0  0.400756  0.166916 -1.553089  0.425724  0.125546   
max     312.0    1041.0  0.625786  0.635866  0.033085  0.623874  0.598896   

     pose_z_1  pose_x_2  pose_y_2  pose_z_2  pose_x_3  pose_y_3  pose_z_3  \
min -1.492318  0.436258  0.126034 -1.492316  0.446727  0.127092 -1.492539   
max  0.025842  0.626072  0.599079  0.026342  0.629794  0.599594  0.026758   

     pose_x_4  pose_y_4  pose_z_4  pose_x_5  pose_y_5  pose_z_5  pose_x_6  \
min  0.402403  0.126298 -1.497166  0.396417  0.127420 -1.497779  0.385016   
max  0.610647  0.601252  0.018466  0.600654  0.603064  0.018762  0.587398   

     pose_y_6  pose_z_6  pose_x_7  pose_y_7  pose_z_7  pose_x_8  pose_y_8  \
min  0.128342 -1.498351  0.463372  0.158492 -1.143188  0.360619  0.167817   
max  0.604734  0.018976  0.648783  0.633478  0.266045  0.558817  0.642008   

     pose_z_8  pose_x_9  pose_y_9  pose_z_9  pose_x_10  pose_y_10  pose_z_10  \
min -1.161080  0.426335  0.229903 -1.425301   0.396070   0.225882  -1.431197   
max  0.225459  0.610005  0.677702  0.070251   0.595146   0.679721   0.056474   

     pose_x_11  pose_y_11  pose_z_11  pose_x_12  pose_y_12  pose_z_12  \
min   0.483572   0.364869  -0.885063   0.269604   0.335885  -0.919410   
max   0.760228   0.822066   0.501943   0.540450   0.842032   0.228361   

     pose_x_13  pose_y_13  pose_z_13  pose_x_14  pose_y_14  pose_z_14  \
min   0.463102   0.299781  -1.219522   0.045958   0.157099  -1.368469   
max   0.965017   1.157535   0.914873   0.541236   1.080209   0.363086   

     pose_x_15  pose_y_15  pose_z_15  pose_x_16  pose_y_16  pose_z_16  \
min   0.303024   0.101773  -2.047556   0.037753  -0.090714  -2.032341   
max   0.957804   1.465627   1.410308   0.684366   1.363703   0.493456   

     pose_x_17  pose_y_17  pose_z_17  pose_x_18  pose_y_18  pose_z_18  \
min   0.226871   0.053381  -2.222781   0.005813  -0.187184   -2.19737   
max   0.998382   1.584232   1.488692   0.759280   1.476210    0.51390   

     pose_x_19  pose_y_19  pose_z_19  pose_x_20  pose_y_20  pose_z_20  \
min   0.223575   0.055556  -2.124815   0.019857  -0.197428  -2.117968   
max   0.982839   1.566418   1.539688   0.762159   1.466434   0.574947   

     pose_x_21  pose_y_21  pose_z_21  pose_x_22  pose_y_22  pose_z_22  \
min   0.254046   0.075403  -2.027537   0.035015  -0.178612  -2.005402   
max   0.949371   1.522125   1.421309   0.733528   1.422319   0.517983   

     pose_x_23  pose_y_23  pose_z_23  pose_x_24  pose_y_24  pose_z_24  \
min   0.470202   0.787004  -0.191999   0.283359   0.784116  -0.282395   
max   0.693827   1.636412   0.285752   0.548747   1.652182   0.194716   

     pose_x_25  pose_y_25  pose_z_25  pose_x_26  pose_y_26  pose_z_26  \
min   0.434065   0.857777  -0.715052   0.235276   0.900589  -0.554788   
max   0.705995   2.029356   0.309713   0.534890   2.024028   0.516914   

     pose_x_27  pose_y_27  pose_z_27  pose_x_28  pose_y_28  pose_z_28  \
min   0.402220   0.841877  -0.238291   0.210542    0.71816  -0.431820   
max   0.738472   2.582700   1.177200   0.542781    2.58546   1.151106   

     pose_x_29  pose_y_29  pose_z_29  pose_x_30  pose_y_30  pose_z_30  \
min   0.392464   0.866249  -0.229169   0.203161   0.732369  -0.437840   
max   0.745149   2.674441   1.251456   0.542724   2.673309   1.212368   

     pose_x_31  pose_y_31  pose_z_31  pose_x_32  pose_y_32  pose_z_32  \
min   0.369476   0.717776  -0.676857   0.220356   0.548145  -0.900088   
max   0.770745   2.753908   0.891101   0.602507   2.764014   0.780514   

     left_hand_x_0  left_hand_y_0  left_hand_z_0  left_hand_x_1  \
min       0.304418       0.061684  -5.839584e-07       0.281701   
max       0.955669       1.287593   7.996486e-07       0.924720   

     left_hand_y_1  left_hand_z_1  left_hand_x_2  left_hand_y_2  \
min       0.036760      -0.050576       0.241463       0.039964   
max       1.155031       0.058045       0.959256       1.075070   

     left_ha

In [18]:
import numpy as np

# Selecionar apenas as colunas numéricas
df_numeric = df_landmarks.iloc[:, 5:]

# Excluir colunas que contêm valores nulos
df_numeric_cleaned = df_numeric.fillna(0)

# Verificar se o DataFrame não está vazio
if not df_numeric_cleaned.empty:
    # Verificar o valor mínimo de todo o dataset
    min_value = df_numeric_cleaned.values.min()

    # Verificar o valor máximo de todo o dataset
    max_value = df_numeric_cleaned.values.max()

    print(f"O valor mínimo em todo o dataset é: {min_value}")
    print(f"O valor máximo em todo o dataset é: {max_value}")
else:
    print("O DataFrame está vazio após a remoção das colunas com valores nulos.")


O valor mínimo em todo o dataset é: -2.222781181335449
O valor máximo em todo o dataset é: 2.7640140056610107


In [19]:
# Preencher os valores nulos com 3 (valor não presente no dataset)

df_landmarks = df_landmarks.fillna(3)
df_landmarks.head(5)

row_id        video_name  video_id    class  frame_id  pose_x_0  \
0  0-abacaxi-0  INES_abacaxi.mp4         0  abacaxi         0  0.495696   
1  0-abacaxi-1  INES_abacaxi.mp4         0  abacaxi         1  0.495288   
2  0-abacaxi-2  INES_abacaxi.mp4         0  abacaxi         2  0.495044   
3  0-abacaxi-3  INES_abacaxi.mp4         0  abacaxi         3  0.495121   
4  0-abacaxi-4  INES_abacaxi.mp4         0  abacaxi         4  0.495188   

   pose_y_0  pose_z_0  pose_x_1  pose_y_1  pose_z_1  pose_x_2  pose_y_2  \
0  0.251119 -1.002079  0.521189  0.209761 -0.950463  0.533843  0.210290   
1  0.252841 -1.023815  0.520663  0.213098 -0.972513  0.533857  0.213758   
2  0.253372 -1.046565  0.520381  0.214643 -0.995046  0.533899  0.215396   
3  0.253392 -1.043955  0.520395  0.214777 -0.992153  0.534221  0.215514   
4  0.252976 -1.012853  0.520400  0.214682 -0.960610  0.534458  0.215453   

   pose_z_2  pose_x_3  pose_y_3  pose_z_3  pose_x_4  pose_y_4  pose_z_4  \
0 -0.950714  0.545261  0.212878 -0.950727  0.475877  0.212704 -0.947200   
1 -0.972775  0.545182  0.215439 -0.972803  0.475431  0.215584 -0.967649   
2 -0.995281  0.545160  0.216666 -0.995289  0.475202  0.216619 -0.990622   
3 -0.992404  0.545196  0.216702 -0.992438  0.475215  0.216841 -0.988482   
4 -0.960871  0.545223  0.216593 -0.960911  0.475224  0.216627 -0.957046   

   pose_x_5  pose_y_5  pose_z_5  pose_x_6  pose_y_6  pose_z_6  pose_x_7  \
0  0.463136  0.214114 -0.947133  0.449410  0.217801 -0.947687  0.568593   
1  0.462078  0.217285 -0.967517  0.449261  0.219710 -0.968047  0.568426   
2  0.461485  0.218336 -0.990460  0.449155  0.220254 -0.990963  0.568391   
3  0.461473  0.218645 -0.988361  0.449155  0.220443 -0.988881  0.568374   
4  0.461457  0.218357 -0.956863  0.449151  0.220112 -0.957363  0.568372   

   pose_y_7  pose_z_7  pose_x_8  pose_y_8  pose_z_8  pose_x_9  pose_y_9  \
0  0.239211 -0.606676  0.438194  0.247255 -0.582871  0.526797  0.307200   
1  0.241346 -0.622200  0.438184  0.247786 -0.589336  0.526384  0.308975   
2  0.242590 -0.642147  0.438184  0.247866 -0.609594  0.526088  0.309600   
3  0.242763 -0.640178  0.438197  0.247868 -0.611365  0.526090  0.309667   
4  0.242768 -0.613345  0.438202  0.247498 -0.584008  0.526091  0.309416   

   pose_z_9  pose_x_10  pose_y_10  pose_z_10  pose_x_11  pose_y_11  pose_z_11  \
0 -0.875365   0.471233   0.309380  -0.868394   0.678584   0.549230  -0.385215   
1 -0.894940   0.469505   0.311069  -0.885050   0.678677   0.549743  -0.396438   
2 -0.917403   0.468491   0.311584  -0.907750   0.678793   0.550119  -0.412349   
3 -0.914945   0.468413   0.311771  -0.906412   0.678798   0.550017  -0.412191   
4 -0.886539   0.468346   0.311608  -0.877740   0.678863   0.549439  -0.396280   

   pose_x_12  pose_y_12  pose_z_12  pose_x_13  pose_y_13  pose_z_13  \
0   0.340820   0.535919  -0.348497   0.732885   0.914818  -0.342786   
1   0.340721   0.535921  -0.355200   0.732540   0.917953  -0.342048   
2   0.340644   0.535930  -0.383089   0.732493   0.920810  -0.345079   
3   0.340651   0.536010  -0.384030   0.732280   0.921365  -0.346550   
4   0.340753   0.536106  -0.374324   0.731608   0.921345  -0.327906   

   pose_x_14  pose_y_14  pose_z_14  pose_x_15  pose_y_15  pose_z_15  \
0   0.284963   0.897970  -0.278457   0.760130   1.175227  -0.769186   
1   0.284964   0.898140  -0.278857   0.760292   1.188829  -0.748641   
2   0.284964   0.898274  -0.300990   0.761115   1.196293  -0.747695   
3   0.285392   0.898343  -0.304133   0.758980   1.195107  -0.749362   
4   0.285404   0.900387  -0.296143   0.756870   1.194275  -0.724050   

   pose_x_16  pose_y_16  pose_z_16  pose_x_17  pose_y_17  pose_z_17  \
0   0.243029   1.153512  -0.695576   0.773915   1.271270  -0.890982   
1   0.243005   1.153649  -0.696378   0.774294   1.286058  -0.869075   
2   0.242966   1.158451  -0.713334   0.775510   1.294023  -0.867836   
3   0.244254   1.159555  -0.715063   0.773296   1.293015  -0.869765   
4   0.246114   1.159675  -0.703363   0.768647   1.291963 

In [20]:
# Salvar o DataFrame em um arquivo CSV
df_landmarks.to_csv('landmarks_named_cleaned.csv', index=False)